# Spotify Popularity Predictor (39%)

The goal is to create a model that predicts the popularity of a song based on its features.

The dataset contains a list of tracks with the following characteristics:
- `acousticness`: whether the track is acoustic
- `danceability`: describes how suitable a track is for dancing
- `duration_ms`: duration of the track in milliseconds
- `energy`: represents a perceptual measure of intensity and activity
- `explicit`: whether the track has explicit lyrics
- `id`: id for the track
- `instrumentalness`: predicts whether a track contains no vocals
- `key`: the key the track is in
- `liveness`: detects the presence of an audience in the recording
- `loudness`: the overall loudness of a track in decibels
- `mode`: modality of a track
- `name`: name of the track
- `popularity`: popularity of the track
- `release_date`: release date
- `speechiness`: detects the presence of spoken words in a track
- `tempo`: overall estimated tempo of a track in beats per minute
- `valence`: describes the musical positiveness conveyed by a track
- `artist`: artist who performed the track

# Model

## Data collection

📝 **Load the `spotify_popularity_train.csv` dataset**
- Display the first few rows
- Perform the basic cleaning operations (remove redundant lines, as well as those with missing values)
- Store the result in a `DataFrame` named `data`

In [ ]:
url = "https://wagon-public-datasets.s3.amazonaws.com/certification_paris_2021Q1/spotify_popularity_train.csv"

In [ ]:
import pandas as pd
data = pd.read_csv(url)

data.head()

In [ ]:
data.shape

In [ ]:
data.drop_duplicates(inplace=True)

In [ ]:
data.isnull().sum().sort_values(ascending=False)/len(data)

In [ ]:
#Mask to drop the rows without artist name
#data = data[~data.artist.isnull()]
data = data.dropna()  

In [ ]:
data.isnull().sum().sort_values(ascending=False)/len(data)

🧪 **Run the following cell to save your results**

In [ ]:
from nbresult import ChallengeResult

ChallengeResult(
    "data_cleaning",
    shape=data.shape).write()

## Simple model

In [13]:
scoring = "neg_root_mean_squared_error"

this metric:
    Strongly penalize largest errors
    Measure errors in the same unit than popularity
    Is better when greater (metric_good_model > metric_bad_model)

**📝 Let's build a first simple linear model using only the numerical features in our dataset to start with**

In [14]:
X_simple = data.drop(['name', 'popularity','artist','id','release_date'], axis = 1)

In [15]:
y = data[['popularity']]

### Holdout evaluation

**📝 Create the 4 variables `X_train_simple` `y_train`, `X_test_simple`, `y_test` with a 50% split with random sampling**

In [16]:
from sklearn.model_selection import train_test_split
X_train_simple, X_test_simple, y_train, y_test = train_test_split(X_simple, y, test_size=0.5, random_state=42)

**📝 Fit and evaluate a basic linear model with this holdout method**`

In [17]:
from sklearn.linear_model import LinearRegression
model = LinearRegression() 
model.fit(X_train_simple, y_train) # Train model
y_pred = model.predict(X_test_simple)

In [18]:
from sklearn.metrics import mean_squared_error
result=-mean_squared_error(y_test, y_pred,squared=False)

In [19]:
result

-18.391930486295614

In [20]:
score_simple_holdout = result

### Cross-validation evaluation

📝 **Let's be sure our score is representative**: 
- 5-times cross validate a basic linear model on the whole numeric dataset (`X_simple`, `y`)
- Do not fine tune the model
- Mean performance is stored in a variable `score_simple_cv_mean` as a `float`
- Standard deviation of the performances is in a float variable `score_simple_cv_std`

In [21]:
from sklearn.model_selection import cross_val_score
scores = cross_val_score(model, X_simple, y, cv=5, scoring=scoring)

In [22]:
score_simple_cv_mean = scores.mean()

In [23]:
score_simple_cv_mean

-18.36055855156951

In [24]:
score_simple_cv_std = scores.std()

🧪 **Run the following cell to save your results**

In [25]:
from nbresult import ChallengeResult

ChallengeResult(
    "simple_model",
    scoring=scoring,
    shape_train = X_train_simple.shape,
    score_simple_holdout=score_simple_holdout,
    score_simple_cv_mean=score_simple_cv_mean,
    score_simple_cv_std=score_simple_cv_std,
).write()

## Feature engineering

Let's try to improve performance using the feature `release_date`

**📝 Create `X_engineered` by adding a new column `year` to `X`, containing the release year of the track as `integer`**

In [26]:
data['year'] = pd.to_datetime(data.release_date).dt.year

In [27]:
X_engineered = data.drop(['name', 'popularity','artist','id','release_date'], axis = 1)

In [28]:
X_engineered.head(2)

acousticness  danceability  duration_ms  energy  explicit  \
0       0.65400         0.499       219827   0.190         0   
1       0.00592         0.439       483948   0.808         0   

   instrumentalness  key  liveness  loudness  mode  speechiness   tempo  \
0           0.00409    7    0.0898   -16.435     1       0.0454  149.46   
1           0.14000    2    0.0890    -8.497     1       0.0677  138.04   

   valence  year  
0   0.4300  1971  
1   0.0587  2015

📝 **Let's see how this impact the performance of our model.**
- Retrain the same simple linear model on numerical values only, adding the new feature `year`
- Save the mean cross-validated performance metric in a variable named `score_engineered` as a `float`
- Do not fine tune the model yet

In [29]:
scores2 = cross_val_score(model, X_engineered, y, cv=5, scoring=scoring)

In [30]:
score_engineered = scores2.mean()

In [31]:
score_engineered

-17.301966769706475

🧪 **Run the following cell to save your results**

In [32]:
from nbresult import ChallengeResult

ChallengeResult("feature_engineering",
    cols = X_engineered.columns,
    years = X_engineered.get("year"),
    score_engineered=score_engineered
).write()

## Pipelining

Let's now look for maximum performance by creating a solid preprocessing pipeline.

**📝 Create a sklearn preprocessing [pipeline](https://scikit-learn.org/stable/modules/generated/sklearn.pipeline.Pipeline.html) and store it as `preproc`**

In [33]:
# 👉 Do not hesitate to reload a clean new dataset if you need a fresh start.
X = data.drop(['id'], axis = 1)
y = data[['popularity']]

In [34]:
from sklearn.base import BaseEstimator, TransformerMixin

class ArtistPopularityTransformer(BaseEstimator, TransformerMixin):
    """
    Compute, as a new feature of the test set, the mean popularity of 
    all songs made by the artist on the train set.
    """

    def __init__(self):
        pass

    def fit(self, X, y=None):
        """
        process artist mean popularity from artists songs popularity
        process song global mean popularity
        """

        # process artist popularity
        self.artist_popularity = y.groupby(X.artist).agg("mean")
        self.artist_popularity.name = "artist_popularity"

        # process mean popularity
        self.mean_popularity = y.mean()

        return self

    def transform(self, X, y=None):
        """
        apply artist mean popularity vs song global mean popularity to songs
        """

        # inject artist popularity
        X = X.merge(self.artist_popularity, how="left", left_on="artist", right_index=True)
       
        # fills popularity of unknown artists with song global mean popularity
        X.replace(np.nan, self.mean_popularity, inplace=True)

        return X['artist_popularity']

In [35]:
#Checking which columns need to be scaled
X.describe()

acousticness  danceability   duration_ms        energy      explicit  \
count  52053.000000  52053.000000  5.205300e+04  52053.000000  52053.000000   
mean       0.498218      0.536523  2.324970e+05      0.483881      0.069698   
std        0.379814      0.176418  1.433212e+05      0.273028      0.254640   
min        0.000000      0.000000  5.991000e+03      0.000000      0.000000   
25%        0.086700      0.413000  1.664000e+05      0.249000      0.000000   
50%        0.516000      0.548000  2.062130e+05      0.468000      0.000000   
75%        0.893000      0.669000  2.662540e+05      0.713000      0.000000   
max        0.996000      0.986000  4.800118e+06      1.000000      1.000000   

       instrumentalness           key      liveness      loudness  \
count      52053.000000  52053.000000  52053.000000  52053.000000   
mean           0.195664      5.191536      0.211833    -11.745365   
std            0.333686      3.526759      0.180351      5.696061   
min            0.000000      0.000000      0.000000    -60.000000   
25%            0.000000      2.000000      0.099500    -14.913000   
50%            0.000469      5.000000      0.139000    -10.836000   
75%            0.240000      8.000000      0.273000     -7.478000   
max            1.000000     11.000000      0.999000      3.744000   

               mode    popularity   speechiness         tempo       valence  \
count  52053.000000  52053.000000  52053.000000  52053.000000  52053.000000   
mean       0.705665     25.815188      0.106189    117.077248      0.524738   
std        0.455747     21.864219      0.182825     30.266286      0.263819   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      1.000000      0.035200     94.004000      0.312000   
50%        1.000000     26.000000      0.045700    115.939000      0.538000   
75%        1.000000     42.000000      0.076800    135.114000      0.742000   
max        1.000000     96.000000      0.970000    243.507000      1.000000   

               year  
count  52053.000000  
mean    1976.912339  
std       26.851577  
min     1920.000000  
25%     1955.000000  
50%     1977.000000  
75%     1999.000000  
max     2021.000000

In [36]:
X.key.nunique()

12

### Choose a scaler

In [ ]:
X[['acousticness']].boxplot()
X[['acousticness']].plot.hist(bins=10)

In [ ]:
X[['danceability']].boxplot()
X[['danceability']].plot.hist(bins=10)

In [ ]:
#X[X.danceability < 0.05].count()

In [ ]:
X[['duration_ms']].boxplot()
X[['duration_ms']].plot.hist(bins=10)

In [ ]:
X[['energy']].boxplot()
X[['energy']].plot.hist(bins=10)

In [ ]:
X.explicit.nunique()

In [ ]:
X[['instrumentalness']].boxplot()
X[['instrumentalness']].plot.hist(bins=10)

In [ ]:
X[['key']].boxplot()
X[['key']].plot.hist(bins=10)

In [ ]:
X.key.nunique()

In [ ]:
X[['liveness']].boxplot()
X[['liveness']].plot.hist(bins=10)

In [ ]:
X[['loudness']].boxplot()
X[['loudness']].plot.hist(bins=10)

In [ ]:
X[['speechiness']].boxplot()
X[['speechiness']].plot.hist(bins=10)

In [ ]:
X[['tempo']].boxplot()
X[['tempo']].plot.hist(bins=10)

In [ ]:
X[['valence']].boxplot()
X[['valence']].plot.hist(bins=10)

In [ ]:
X[['year']].boxplot()
X[['year']].plot.hist(bins=10)

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns

fig, (ax1) = plt.subplots(ncols=1, figsize=(10, 8))
ax1.set_title('Original Distributions')

sns.kdeplot(X['acousticness'], ax=ax1)
sns.kdeplot(X['danceability'], ax=ax1)
sns.kdeplot(X['duration_ms'], ax=ax1)
sns.kdeplot(X['energy'], ax=ax1)
sns.kdeplot(X['explicit'], ax=ax1)
sns.kdeplot(X['instrumentalness'], ax=ax1)
sns.kdeplot(X['key'], ax=ax1)
sns.kdeplot(X['liveness'], ax=ax1)
sns.kdeplot(X['loudness'], ax=ax1)
sns.kdeplot(X['mode'], ax=ax1)
sns.kdeplot(X['speechiness'], ax=ax1)
sns.kdeplot(X['tempo'], ax=ax1)
sns.kdeplot(X['valence'], ax=ax1)
sns.kdeplot(X['year'], ax=ax1)

In [ ]:
#col_names = list(X.columns)

### Pipeline

In [37]:
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import MinMaxScaler, RobustScaler, StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import FunctionTransformer
import numpy as np

year_constructor = FunctionTransformer(lambda df: pd.DataFrame\
                                        ([pd.to_datetime(date).year for date in df.release_date]))
drop_some_col = FunctionTransformer(lambda df: df.drop(columns=['id','name','release_date','artist']))

#artist_preproc = Pipeline([
    #('artist_popularity', ArtistPopularityTransformer()),
    #('scaler', MinMaxScaler())])

year_preproc = Pipeline([
    ('year', year_constructor),
    ('scaler', MinMaxScaler())
])

r_transformer = Pipeline([
    ('scaler3', RobustScaler()),
    ])

mm_transformer = Pipeline([
    ('scaler2', MinMaxScaler()),
    ])

# Encode categorical variables
cat_transformer = OneHotEncoder(handle_unknown='ignore')

# Paralellize "num_transformer" and "One hot encoder"
preproc = ColumnTransformer([
    #('artist_preproc', artist_preproc, ['artist']),
    ('year_preproc', year_preproc, ['release_date']), 
    ('mm_transformer', mm_transformer, ['duration_ms','loudness','tempo','year']),
    ('r_transformer', r_transformer, ['acousticness','danceability','energy','instrumentalness','liveness','speechiness','valence']),
    ('cat_transformer', cat_transformer, ['explicit','key','mode'])])

In [ ]:

#Creating the preprocessor, composed of other pipelines
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import FunctionTransformer
from sklearn.preprocessing import StandardScaler, MinMaxScaler, RobustScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.compose import ColumnTransformer
import numpy as np

year_constructor = FunctionTransformer(lambda df: pd.DataFrame\
                                        ([pd.to_datetime(date).year for date in df.release_date]))
drop_some_col = FunctionTransformer(lambda df: df.drop(columns=['id','name','release_date','artist']))

#artist_preproc = Pipeline([
    #('artist_popularity', ArtistPopularityTransformer()),
    #('scaler', MinMaxScaler())])

year_preproc = Pipeline([
    ('year', year_constructor),
    ('scaler', MinMaxScaler())
])

other_preproc = ColumnTransformer([
    ('scaling', RobustScaler(), ['duration_ms','loudness','tempo']),
    ('encoding', OneHotEncoder(sparse = False), ['key'])],
    remainder = 'passthrough')

preproc = ColumnTransformer([
    #('artist_preproc', artist_preproc, ['artist']),
    ('year_preproc', year_preproc, ['release_date']),
    ('other_preproc', other_preproc, ['acousticness', 'danceability', 'duration_ms', 'energy', 'explicit',
               'instrumentalness', 'key', 'liveness', 'loudness', 'mode','speechiness', 'tempo', 'valence'])
])

In [38]:
preproc.fit_transform(X,y)

array([[0.5049505 , 0.04460374, 0.68343687, ..., 0.        , 0.        ,
        1.        ],
       [0.94059406, 0.09969636, 0.80796624, ..., 0.        , 0.        ,
        1.        ],
       [0.47524752, 0.04999909, 0.7607618 , ..., 0.        , 0.        ,
        1.        ],
       ...,
       [0.99009901, 0.06358801, 0.85736697, ..., 0.        , 0.        ,
        1.        ],
       [0.31683168, 0.04390831, 0.61160266, ..., 0.        , 0.        ,
        1.        ],
       [0.72277228, 0.04434217, 0.70464671, ..., 0.        , 1.        ,
        0.        ]])

In [39]:
pd.set_option('display.max_columns', None)
pd.options.display.max_rows = 4000

In [40]:
pd.DataFrame(preproc.fit_transform(X))

0         1         2         3         4         5         6   \
0      0.504950  0.044604  0.683437  0.613781  0.504950  0.171152 -0.191406   
1      0.940594  0.099696  0.807966  0.566883  0.940594 -0.632618 -0.425781   
2      0.475248  0.049999  0.760762  0.311568  0.475248  0.270371 -0.097656   
3      0.059406  0.025872  0.604653  0.596833  0.059406 -0.107900  0.519531   
4      0.871287  0.025828  0.825584  0.571942  0.871287  0.057051 -0.019531   
5      0.653465  0.046620  0.683358  0.486684  0.653465 -0.602133 -0.710937   
6      0.425743  0.091300  0.739928  0.459198  0.425743  0.233164  0.113281   
7      0.574257  0.067732  0.754408  0.456578  0.574257 -0.472529  0.687500   
8      0.891089  0.050962  0.874969  0.574850  0.891089 -0.618380  0.671875   
9      0.415842  0.037242  0.633126  0.353136  0.415842  0.548183 -1.117187   
10     0.990099  0.021634  0.814194  0.328783  0.990099 -0.522634  1.304688   
11     0.297030  0.019472  0.690026  0.542173  0.297030  0.153789  0.628906   
12     0.445545  0.031777  0.779430  0.495440  0.445545  0.279052  0.507812   
13     0.346535  0.037181  0.708475  0.391151  0.346535  0.472529  0.695312   
14     0.990099  0.091277  0.814147  0.595568  0.990099 -0.612923  0.039063   
15     0.099010  0.047730  0.765813  0.300205  0.099010  0.549423  0.031250   
16     0.980198  0.044742  0.818430  0.456669  0.980198  0.533300  0.734375   
17     0.732673  0.067885  0.850166  0.410259  0.732673 -0.639581 -0.027344   
18     0.297030  0.592326  0.671044  0.341846  0.297030  0.475009  0.328125   
19     0.584158  0.079674  0.862795  0.810260  0.584158 -0.610195 -1.160156   
20     0.356436  0.038997  0.676974  0.323436  0.356436  0.591591 -1.074219   
21     0.198020  0.028232  0.602927  0.309543  0.198020  0.571747 -0.687500   
22     0.762376  0.019957  0.813175  0.434698  0.762376 -0.639787 -0.859375   
23     0.039604  0.033446  0.765547  0.778565  0.039604  0.462607 -0.492187   
24     0.425743  0.030503  0.715769  0.491238  0.425743  0.153789  0.605469   
25     0.405941  0.114600  0.610489  0.518227  0.405941  0.558105 -1.472656   
26     0.990099  0.033522  0.880726  0.414777  0.990099 -0.577205  0.664062   
27     0.485149  0.060025  0.684190  0.552255  0.485149 -0.295175 -0.429687   
28     0.386139  0.041233  0.703141  0.273947  0.386139  0.265410 -0.753906   
29     0.980198  0.050778  0.720334  0.331917  0.980198  0.453925 -0.351562   
30     0.316832  0.039183  0.739223  0.326820  0.316832  0.586630 -0.429687   
31     0.544554  0.030873  0.564853  0.402802  0.544554  0.114101  0.398438   
32     0.425743  0.031471  0.781360  0.305318  0.425743  0.261689 -0.167969   
33     0.099010  0.036649  0.750345  0.455354  0.099010  0.594072 -0.695312   
34     0.950495  0.033068  0.863328  0.334725  0.950495 -0.600521  0.656250   
35     0.415842  0.036227  0.794585  0.742648  0.415842  0.065732 -0.867187   
36     0.485149  0.087133  0.766190  0.450106  0.485149  0.166191  0.195313   
37     0.693069  0.023678  0.528881  0.699783  0.693069  0.426640 -1.819141   
38     0.702970  0.033516  0.784874  0.403820  0.702970  0.347265  0.734375   
39     0.910891  0.023737  0.810931  0.621136  0.910891  0.432841  0.386719   
40     0.148515  0.059561  0.740760  0.472032  0.148515  0.590351 -0.496094   
41     0.663366  0.042345  0.534764  0.590295  0.663366  0.594072 -0.460937   
42     0.475248  0.032191  0.803432  0.264576  0.475248 -0.256728 -0.890625   
43     0.356436  0.030881  0.551895  0.327399  0.356436  0.481210 -1.847656   
44     0.594059  0.042017  0.543267  0.336315  0.594059 -0.155029 -1.531250   
45     0.742574  0.035490  0.844299  0.335013  0.742574 -0.441523  0.015625   
46     0.752475  0.060306  0.844644  0.484623  0.752475 -0.639911 -0.171875   
47     0.772277  0.053581  0.805801  0.579215  0.772277 -0.468808  0.062500   
48     0.257426  0.030870  0.502400  0.320656  0.257426  0.589111 -0.769531   
49     0.386139  0.034580  0.794334  0.425339  0.386139  0.1785

In [41]:
np.shape(preproc.fit_transform(X, y))

(52053, 28)

**📝 Store the number of columns/feature after preprocessing your inputs in a variable `col_number`**

In [42]:
col_number=28

🧪 **Run the following cells to save your results**

In [43]:
# Visually print your preproc
from sklearn import set_config; set_config(display='diagram')
preproc

ColumnTransformer(transformers=[('year_preproc',
                                 Pipeline(steps=[('year',
                                                  FunctionTransformer(func=<function <lambda> at 0x000001391C311EA0>)),
                                                 ('scaler', MinMaxScaler())]),
                                 ['release_date']),
                                ('mm_transformer',
                                 Pipeline(steps=[('scaler2', MinMaxScaler())]),
                                 ['duration_ms', 'loudness', 'tempo', 'year']),
                                ('r_transformer',
                                 Pipeline(steps=[('scaler3', RobustScaler())]),
                                 ['acousticness', 'danceability', 'energy',
                                  'instrumentalness', 'liveness', 'speechiness',
                                  'valence']),
                                ('cat_transformer',
                                 OneHotEncoder(handle_unknown='ignore'),
                                 ['explicit', 'key', 'mode'])])

In [44]:
# Save your preproc
from nbresult import ChallengeResult

ChallengeResult(
    "preprocessing",
    col_number=col_number,
    first_observation = preproc.fit_transform(X, y)[0]
).write()

## Training

📝 **Time to fine tune your models**

- Add an **estimator** to your pipeline (only from Scikit-learn) 

- Train your pipeline and **fine-tune** (optimize) your estimator to maximize prediction score

- You must try to fine tune at least 2 different models: 
    - create one pipeline with a **linear model** of your choice
    - create one pipeline with an **ensemble model** of your choice

Then, 

- Save your two best 5-time cross-validated scores as _float_: `score_linear` and `score_ensemble`

- Save your two best trained pipelines as _Pipeline_ objects: `pipe_linear` and `pipe_ensemble`

### Linear

In [45]:
from sklearn.linear_model import Ridge
final_pipe = Pipeline([
    ('preprocessing', preproc),
    ('linear_regression', Ridge())])

In [46]:
score_linear = cross_val_score(final_pipe, X, y, cv=5, scoring=scoring).mean()
score_linear

-17.30364031959535

In [47]:
#pipe_linear.get_params()

In [53]:
from sklearn.model_selection import GridSearchCV

grid_search = GridSearchCV(
    final_pipe, 
    param_grid={
        # Access any component of the pipeline, as far back as you want
        'linear_regression__alpha': [10]},
    cv=5,
    scoring=scoring)

grid_search.fit(X, y)

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('preprocessing',
                                        ColumnTransformer(transformers=[('year_preproc',
                                                                         Pipeline(steps=[('year',
                                                                                          FunctionTransformer(func=<function <lambda> at 0x000001391C311EA0>)),
                                                                                         ('scaler',
                                                                                          MinMaxScaler())]),
                                                                         ['release_date']),
                                                                        ('mm_transformer',
                                                                         Pipeline(steps=[('scaler2',
                                                                                          MinMaxScaler())]),
                                                                         ['duration_ms',
                                                                          'loudness',
                                                                          'tempo',
                                                                          'year']),
                                                                        ('r_transformer',
                                                                         Pipeline(steps=[('scaler3',
                                                                                          RobustScaler())]),
                                                                         ['acousticness',
                                                                          'danceability',
                                                                          'energy',
                                                                          'instrumentalness',
                                                                          'liveness',
                                                                          'speechiness',
                                                                          'valence']),
                                                                        ('cat_transformer',
                                                                         OneHotEncoder(handle_unknown='ignore'),
                                                                         ['explicit',
                                                                          'key',
                                                                          'mode'])])),
                                       ('linear_regression', Ridge())]),
             param_grid={'linear_regression__alpha': [10]},
             scoring='neg_root_mean_squared_error')

In [54]:
grid_search.best_params_

{'linear_regression__alpha': 10}

In [55]:
grid_search.best_score_

-17.303563637692683

### Ensemble

In [51]:
from sklearn.tree import DecisionTreeRegressor
pipe_ensemble = Pipeline([
    ('preprocessor', preproc),
    ('model', DecisionTreeRegressor())
])

score_ensemble = cross_val_score(pipe_ensemble, X, y, cv=5, scoring=scoring).mean()
score_ensemble

-18.18811969052563

In [57]:
from sklearn.ensemble import GradientBoostingRegressor

final_pipe2 = Pipeline([
    ('preprocessing', preproc),
    ('GBR', GradientBoostingRegressor(
    n_estimators=100, 
    learning_rate=0.1
))])

#pipe_ensemble = final_pipe2.fit(X_train,y_train)
#pipe_ensemble.predict(X_test)
#pipe_ensemble.score(X_test,y_test)

# Cross validate pipeline
score_ensemble2 = cross_val_score(final_pipe2, X, y, cv=5, scoring=scoring).mean()
score_ensemble2


C:\Users\mvalyashova\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
C:\Users\mvalyashova\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
C:\Users\mvalyashova\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
C:\Users\mvalyashova\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A col

-13.496657134858603

In [58]:
#Tuning of the ensemble pipeline
grid_search2 = GridSearchCV(
    pipe_ensemble, 
    param_grid={
        'model__min_samples_split': [20], #[1,2,10]
        'model__max_depth': [8]},#[4,8,16] [6, 8, 10]
    cv=5,
    scoring=scoring)
grid_search2.fit(X,y);
grid_search2.best_params_ , grid_search2.best_score_

({'model__max_depth': 8, 'model__min_samples_split': 20}, -14.002940543063966)

In [59]:
score_ensemble = grid_search2.best_score_

🧪 **Run the following cells to save your results**

In [61]:
# Print below your best pipe for correction purpose
from sklearn import set_config; set_config(display='diagram')
#pipe_linear

In [62]:
# Print below your best pipe for correction purpose
pipe_ensemble

Pipeline(steps=[('preprocessor',
                 ColumnTransformer(transformers=[('year_preproc',
                                                  Pipeline(steps=[('year',
                                                                   FunctionTransformer(func=<function <lambda> at 0x000001391C311EA0>)),
                                                                  ('scaler',
                                                                   MinMaxScaler())]),
                                                  ['release_date']),
                                                 ('mm_transformer',
                                                  Pipeline(steps=[('scaler2',
                                                                   MinMaxScaler())]),
                                                  ['duration_ms', 'loudness',
                                                   'tempo', 'year']),
                                                 ('r_transformer',
                                                  Pipeline(steps=[('scaler3',
                                                                   RobustScaler())]),
                                                  ['acousticness',
                                                   'danceability', 'energy',
                                                   'instrumentalness',
                                                   'liveness', 'speechiness',
                                                   'valence']),
                                                 ('cat_transformer',
                                                  OneHotEncoder(handle_unknown='ignore'),
                                                  ['explicit', 'key',
                                                   'mode'])])),
                ('model', DecisionTreeRegressor())])

In [63]:
from nbresult import ChallengeResult

ChallengeResult("model_tuning",
    scoring = scoring,
    score_linear=score_linear,
    score_ensemble=score_ensemble).write()